# Structured Streaming using the Python DataFrames API

Apache Spark includes a high-level stream processing API, [Structured Streaming](http://spark.apache.org/docs/latest/structured-streaming-programming-guide.html). In this notebook we take a quick look at how to use the DataFrame API to build Structured Streaming applications. We want to compute real-time metrics like running counts and windowed counts on a stream of timestamped actions (e.g. Open, Close, etc).

To run this notebook, import it and attach it to a Spark cluster.

## Sample Data
We have some sample action data as files in `/databricks-datasets/structured-streaming/events/` which we are going to use to build this appication. Let's take a look at the contents of this directory.

In [0]:
# Look at the content of the following folder: /databricks-datasets/structured-streaming/events/
# What do you see?
display(dbutils.fs.ls("/databricks-datasets/structured-streaming/events/"))

path name size modificationTime dbfs:/databricks-datasets/structured-streaming/events/file-0.json file-0.json 72530 1469673865000 dbfs:/databricks-datasets/structured-streaming/events/file-1.json file-1.json 72961 1469673866000 dbfs:/databricks-datasets/structured-streaming/events/file-10.json file-10.json 73025 1469673878000 dbfs:/databricks-datasets/structured-streaming/events/file-11.json file-11.json 72999 1469673879000 dbfs:/databricks-datasets/structured-streaming/events/file-12.json file-12.json 72987 1469673880000 dbfs:/databricks-datasets/structured-streaming/events/file-13.json file-13.json 73006 1469673881000 dbfs:/databricks-datasets/structured-streaming/events/file-14.json file-14.json 73003 1469673882000 dbfs:/databricks-datasets/structured-streaming/events/file-15.json file-15.json 73007 1469673883000 dbfs:/databricks-datasets/structured-streaming/events/file-16.json file-16.json 72978 1469673885000 dbfs:/databricks-datasets/structured-streaming/events/file-17.json file-17.json 73008 1469673886000 dbfs:/databricks-datasets/structured-streaming/events/file-18.json file-18.json 73002 1469673887000 dbfs:/databricks-datasets/structured-streaming/events/file-19.json file-19.json 73014 1469673888000 dbfs:/databricks-datasets/structured-streaming/events/file-2.json file-2.json 73007 1469673868000 dbfs:/databricks-datasets/structured-streaming/events/file-20.json file-20.json 72987 1469673889000 dbfs:/databricks-datasets/structured-streaming/events/file-21.json file-21.json 72983 1469673891000 dbfs:/databricks-datasets/structured-streaming/events/file-22.json file-22.json 73009 1469673892000 dbfs:/databricks-datasets/structured-streaming/events/file-23.json file-23.json 72985 1469673893000 dbfs:/databricks-datasets/structured-streaming/events/file-24.json file-24.json 73020 1469673894000 dbfs:/databricks-datasets/structured-streaming/events/file-25.json file-25.json 72980 1469673895000 dbfs:/databricks-datasets/structured-streaming/events/file-26.json file-26.json 73002 1469673897000 dbfs:/databricks-datasets/structured-streaming/events/file-27.json file-27.json 73013 1469673898000 dbfs:/databricks-datasets/structured-streaming/events/file-28.json file-28.json 73005 1469673899000 dbfs:/databricks-datasets/structured-streaming/events/file-29.json file-29.json 72977 1469673900000 dbfs:/databricks-datasets/structured-streaming/events/file-3.json file-3.json 72996 1469673869000 dbfs:/databricks-datasets/structured-streaming/events/file-30.json file-30.json 73009 1469673902000 dbfs:/databricks-datasets/structured-streaming/events/file-31.json file-31.json 73008 1469673903000 dbfs:/databricks-datasets/structured-streaming/events/file-32.json file-32.json 72982 1469673904000 dbfs:/databricks-datasets/structured-streaming/events/file-33.json file-33.json 73033 1469673905000 dbfs:/databricks-datasets/structured-streaming/events/file-34.json file-34.json 72985 1469673907000 dbfs:/databricks-datasets/structured-streaming/events/file-35.json file-35.json 72974 1469673908000 dbfs:/databricks-datasets/structured-streaming/events/file-36.json file-36.json 73013 1469673909000 dbfs:/databricks-datasets/structured-streaming/events/file-37.json file-37.json 72989 1469673910000 dbfs:/databricks-datasets/structured-streaming/events/file-38.json file-38.json 72999 1469673911000 dbfs:/databricks-datasets/structured-streaming/events/file-39.json file-39.json 73013 1469673913000 dbfs:/databricks-datasets/structured-streaming/events/file-4.json file-4.json 72992 1469673870000 dbfs:/databricks-datasets/structured-streaming/events/file-40.json file-40.json 72986 1469673914000 dbfs:/databricks-datasets/structured-streaming/events/file-41.json file-41.json 73019 1469673915000 dbfs:/databricks-datasets/structured-streaming/events/file-42.json file-42.json 72986 1469673916000 dbfs:/databricks-datasets/structured-streaming/events/file-43.json file-43.json 72990 1469673918000 dbfs:/databricks-datasets/structured-streaming/events/file-44.json file-44.jso

There are about 50 JSON files in the directory. Let's see what each JSON file contains.

In [0]:
# Look at the functions head in dbutils
# Open one file
dbutils.help()

This module provides various utilities for users to interact with the rest of Databricks.
 credentials: DatabricksCredentialUtils -> Utilities for interacting with credentials within notebooks data: DataUtils -> Utilities for understanding and interacting with datasets (EXPERIMENTAL) fs: DbfsUtils -> Manipulates the Databricks filesystem (DBFS) from the console jobs: JobsUtils -> Utilities for leveraging jobs features library: LibraryUtils -> Utilities for session isolated libraries meta: MetaUtils -> Methods to hook into the compiler (EXPERIMENTAL) notebook: NotebookUtils -> Utilities for the control flow of a notebook (EXPERIMENTAL) preview: Preview -> Utilities under preview category secrets: SecretUtils -> Provides utilities for leveraging secrets within notebooks widgets: WidgetsUtils -> Methods to create and get bound value of input widgets inside notebooks

Each line in the file contains JSON record with two fields - `time` and `action`. Let's try to analyze these files interactively.

In [0]:
dbutils.fs.help()

dbutils.fs provides utilities for working with FileSystems. Most methods in
this package can take either a DBFS path (e.g., "/foo" or "dbfs:/foo"), or
another FileSystem URI.

For more info about a method, use dbutils.fs.help("methodName") .

In notebooks, you can also use the %fs shorthand to access DBFS. The %fs shorthand maps
straightforwardly onto dbutils calls. For example, "%fs head --maxBytes=10000 /file/path"
translates into "dbutils.fs.head("/file/path", maxBytes = 10000)".
 mount mount(source: String, mountPoint: String, encryptionType: String = "", owner: String = null, extraConfigs: Map = Map.empty[String, String]): boolean -> Mounts the given source directory into DBFS at the given mount point mounts: Seq -> Displays information about what is mounted within DBFS refreshMounts: boolean -> Forces all machines in this cluster to refresh their mount cache, ensuring they receive the most recent information unmount(mountPoint: String): boolean -> Deletes a DBFS mount point updateMount(source: String, mountPoint: String, encryptionType: String = "", owner: String = null, extraConfigs: Map = Map.empty[String, String]): boolean -> Similar to mount(), but updates an existing mount point (if present) instead of creating a new one fsutils cp(from: String, to: String, recurse: boolean = false): boolean -> Copies a file or directory, possibly across FileSystems head(file: String, maxBytes: int = 65536): String -> Returns up to the first 'maxBytes' bytes of the given file as a String encoded in UTF-8 ls(dir: String): Seq -> Lists the contents of a directory mkdirs(dir: String): boolean -> Creates the given directory if it does not exist, also creating any necessary parent directories mv(from: String, to: String, recurse: boolean = false): boolean -> Moves a file or directory, possibly across FileSystems put(file: String, contents: String, overwrite: boolean = false): boolean -> Writes the given String out to a file, encoded in UTF-8 rm(dir: String, recurse: boolean = false): boolean -> Removes a file or directory

## Batch/Interactive Processing
The usual first step in attempting to process the data is to interactively query the data. Let's define a static DataFrame on the files, and give it a table name.

In [0]:
from pyspark.sql.types import *

inputPath = "/databricks-datasets/structured-streaming/events/"

# Since we know the data format already, let's define the schema to speed up processing (no need for Spark to infer schema)
jsonSchema = StructType(
  [ StructField("time", TimestampType(), True),
   StructField("action", StringType(), True) ]
)



In [0]:
# Read all json files, taking into account the defined schema, and display the content 
staticInputDF = spark.read.schema(jsonSchema).json(inputPath)
display(staticInputDF)

time action 2016-07-28T04:19:28.000+0000 Close 2016-07-28T04:19:28.000+0000 Close 2016-07-28T04:19:29.000+0000 Open 2016-07-28T04:19:31.000+0000 Close 2016-07-28T04:19:31.000+0000 Open 2016-07-28T04:19:31.000+0000 Open 2016-07-28T04:19:32.000+0000 Close 2016-07-28T04:19:33.000+0000 Close 2016-07-28T04:19:35.000+0000 Close 2016-07-28T04:19:36.000+0000 Open 2016-07-28T04:19:38.000+0000 Close 2016-07-28T04:19:40.000+0000 Open 2016-07-28T04:19:41.000+0000 Close 2016-07-28T04:19:42.000+0000 Open 2016-07-28T04:19:45.000+0000 Open 2016-07-28T04:19:47.000+0000 Open 2016-07-28T04:19:48.000+0000 Open 2016-07-28T04:19:49.000+0000 Open 2016-07-28T04:19:55.000+0000 Open 2016-07-28T04:20:00.000+0000 Close 2016-07-28T04:20:00.000+0000 Open 2016-07-28T04:20:01.000+0000 Open 2016-07-28T04:20:03.000+0000 Close 2016-07-28T04:20:07.000+0000 Open 2016-07-28T04:20:11.000+0000 Open 2016-07-28T04:20:12.000+0000 Close 2016-07-28T04:20:12.000+0000 Open 2016-07-28T04:20:13.000+0000 Close 2016-07-28T04:20:16.000+0000 Open 2016-07-28T04:20:23.000+0000 Close 2016-07-28T04:20:23.000+0000 Close 2016-07-28T04:20:23.000+0000 Open 2016-07-28T04:20:26.000+0000 Close 2016-07-28T04:20:30.000+0000 Close 2016-07-28T04:20:32.000+0000 Open 2016-07-28T04:20:32.000+0000 Open 2016-07-28T04:20:34.000+0000 Close 2016-07-28T04:20:36.000+0000 Open 2016-07-28T04:20:42.000+0000 Close 2016-07-28T04:20:42.000+0000 Open 2016-07-28T04:20:42.000+0000 Open 2016-07-28T04:20:48.000+0000 Close 2016-07-28T04:20:48.000+0000 Close 2016-07-28T04:20:48.000+0000 Open 2016-07-28T04:20:50.000+0000 Open 2016-07-28T04:20:52.000+0000 Open 2016-07-28T04:20:55.000+0000 Open 2016-07-28T04:20:55.000+0000 Open 2016-07-28T04:20:56.000+0000 Close 2016-07-28T04:20:56.000+0000 Close 2016-07-28T04:20:56.000+0000 Open 2016-07-28T04:20:59.000+0000 Open 2016-07-28T04:20:59.000+0000 Open 2016-07-28T04:21:02.000+0000 Close 2016-07-28T04:21:04.000+0000 Open 2016-07-28T04:21:08.000+0000 Open 2016-07-28T04:21:11.000+0000 Close 2016-07-28T04:21:13.000+0000 Open 2016-07-28T04:21:18.000+0000 Open 2016-07-28T04:21:19.000+0000 Open 2016-07-28T04:21:20.000+0000 Close 2016-07-28T04:21:22.000+0000 Open 2016-07-28T04:21:23.000+0000 Open 2016-07-28T04:21:27.000+0000 Close 2016-07-28T04:21:28.000+0000 Open 2016-07-28T04:21:31.000+0000 Close 2016-07-28T04:21:32.000+0000 Open 2016-07-28T04:21:32.000+0000 Open 2016-07-28T04:21:33.000+0000 Open 2016-07-28T04:21:34.000+0000 Close 2016-07-28T04:21:34.000+0000 Open 2016-07-28T04:21:35.000+0000 Close 2016-07-28T04:21:37.000+0000 Open 2016-07-28T04:21:38.000+0000 Close 2016-07-28T04:21:44.000+0000 Open 2016-07-28T04:21:46.000+0000 Close 2016-07-28T04:21:46.000+0000 Open 2016-07-28T04:21:48.000+0000 Close 2016-07-28T04:21:49.000+0000 Open 2016-07-28T04:21:50.000+0000 Close 2016-07-28T04:21:52.000+0000 Close 2016-07-28T04:21:52.000+0000 Open 2016-07-28T04:21:52.000+0000 Open 2016-07-28T04:21:53.000+0000 Open 2016-07-28T04:21:53.000+0000 Open 2016-07-28T04:21:56.000+0000 Close 2016-07-28T04:21:56.000+0000 Close 2016-07-28T04:21:57.000+0000 Close 2016-07-28T04:21:58.000+0000 Open 2016-07-28T04:21:59.000+0000 Close 2016-07-28T04:22:01.000+0000 Open 2016-07-28T04:22:06.000+0000 Close 2016-07-28T04:22:10.000+0000 Open 2016-07-28T04:22:11.000+0000 Close 2016-07-28T04:22:12.000+0000 Open 2016-07-28T04:22:14.000+0000 Close 2016-07-28T04:22:15.000+0000 Close 2016-07-28T04:22:15.000+0000 Open 2016-07-28T04:22:19.000+0000 Close 2016-07-28T04:22:20.000+0000 Close 2016-07-28T04:22:24.000+0000 Close 2016-07-28T04:22:24.000+0000 Close 2016-07-28T04:22:24.000+0000 Open 2016-07-28T04:22:30.000+0000 Open 2016-07-28T04:22:31.000+0000 Close 2016-07-28T04:22:31.000+0000 Open 2016-07-28T04:22:33.000+0000 Close 2016-07-28T04:22:39.000+0000 Open 2016-07-28T04:22:40.000+0000 Close 2016-07-28T04:22:43.000+0000 Open 2016-07-28T04:22:44.000+0000 Open 2016-07-28T04:22:49.000+0000 Close 2016-07-28T04:22:50.000+0000 Open 2016-07-28T04:22:55.000+0000 Open 2016-07-28T04:22:56.000+0000 Open 2016-07-28T04:22:58.000+0000

- Compare the dates from the output without schema and with it. 
- Did you notice that inputPath is a folder?

**Comparison of dates:**
> - Without schema: Dates are read as strings (StringType), not timestamps.
> - With schema: Dates are properly parsed as TimestampType, enabling time-based operations like windowing.

In [0]:
# Calculate the total number of 'Open' and 'Close' actions 
from pyspark.sql.functions import col

staticInputDF.filter(col("action").isin("Open", "Close")) \
    .groupBy("action") \
    .count() \
    .show()


+------+-----+
|action|count|
+------+-----+
|  Open|50000|
| Close|50000|
+------+-----+



In [0]:
# Determine min and max time
from pyspark.sql.functions import min, max

staticInputDF.select(min("time").alias("min_time"), max("time").alias("max_time")).show()

+-------------------+-------------------+
|           min_time|           max_time|
+-------------------+-------------------+
|2016-07-26 02:45:07|2016-07-28 06:48:19|
+-------------------+-------------------+



In [0]:
# Calculate the number of "open" and "close" actions with one hour windows: staticCountsDF
# Look at groupBy(..., window) function
from pyspark.sql.functions import window, col

staticCountsDF = staticInputDF \
    .filter(col("action").isin("Open", "Close")) \
    .groupBy(
        window(col("time"), "1 hour"),
        col("action")
    ) \
    .count() \
    .orderBy("window")

display(staticCountsDF)

window action count List(2016-07-26T02:00:00.000+0000, 2016-07-26T03:00:00.000+0000) Open 179 List(2016-07-26T02:00:00.000+0000, 2016-07-26T03:00:00.000+0000) Close 11 List(2016-07-26T03:00:00.000+0000, 2016-07-26T04:00:00.000+0000) Close 344 List(2016-07-26T03:00:00.000+0000, 2016-07-26T04:00:00.000+0000) Open 1001 List(2016-07-26T04:00:00.000+0000, 2016-07-26T05:00:00.000+0000) Close 815 List(2016-07-26T04:00:00.000+0000, 2016-07-26T05:00:00.000+0000) Open 999 List(2016-07-26T05:00:00.000+0000, 2016-07-26T06:00:00.000+0000) Close 1003 List(2016-07-26T05:00:00.000+0000, 2016-07-26T06:00:00.000+0000) Open 1000 List(2016-07-26T06:00:00.000+0000, 2016-07-26T07:00:00.000+0000) Open 993 List(2016-07-26T06:00:00.000+0000, 2016-07-26T07:00:00.000+0000) Close 1011 List(2016-07-26T07:00:00.000+0000, 2016-07-26T08:00:00.000+0000) Close 989 List(2016-07-26T07:00:00.000+0000, 2016-07-26T08:00:00.000+0000) Open 1008 List(2016-07-26T08:00:00.000+0000, 2016-07-26T09:00:00.000+0000) Close 985 List(2016-07-26T08:00:00.000+0000, 2016-07-26T09:00:00.000+0000) Open 996 List(2016-07-26T09:00:00.000+0000, 2016-07-26T10:00:00.000+0000) Open 1000 List(2016-07-26T09:00:00.000+0000, 2016-07-26T10:00:00.000+0000) Close 983 List(2016-07-26T10:00:00.000+0000, 2016-07-26T11:00:00.000+0000) Close 1022 List(2016-07-26T10:00:00.000+0000, 2016-07-26T11:00:00.000+0000) Open 1007 List(2016-07-26T11:00:00.000+0000, 2016-07-26T12:00:00.000+0000) Open 991 List(2016-07-26T11:00:00.000+0000, 2016-07-26T12:00:00.000+0000) Close 1028 List(2016-07-26T12:00:00.000+0000, 2016-07-26T13:00:00.000+0000) Close 960 List(2016-07-26T12:00:00.000+0000, 2016-07-26T13:00:00.000+0000) Open 996 List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) Close 1028 List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) Open 1006 List(2016-07-26T14:00:00.000+0000, 2016-07-26T15:00:00.000+0000) Close 994 List(2016-07-26T14:00:00.000+0000, 2016-07-26T15:00:00.000+0000) Open 991 List(2016-07-26T15:00:00.000+0000, 2016-07-26T16:00:00.000+0000) Close 988 List(2016-07-26T15:00:00.000+0000, 2016-07-26T16:00:00.000+0000) Open 1020 List(2016-07-26T16:00:00.000+0000, 2016-07-26T17:00:00.000+0000) Close 984 List(2016-07-26T16:00:00.000+0000, 2016-07-26T17:00:00.000+0000) Open 992 List(2016-07-26T17:00:00.000+0000, 2016-07-26T18:00:00.000+0000) Open 990 List(2016-07-26T17:00:00.000+0000, 2016-07-26T18:00:00.000+0000) Close 1036 List(2016-07-26T18:00:00.000+0000, 2016-07-26T19:00:00.000+0000) Close 1001 List(2016-07-26T18:00:00.000+0000, 2016-07-26T19:00:00.000+0000) Open 1004 List(2016-07-26T19:00:00.000+0000, 2016-07-26T20:00:00.000+0000) Close 967 List(2016-07-26T19:00:00.000+0000, 2016-07-26T20:00:00.000+0000) Open 998 List(2016-07-26T20:00:00.000+0000, 2016-07-26T21:00:00.000+0000) Open 1010 List(2016-07-26T20:00:00.000+0000, 2016-07-26T21:00:00.000+0000) Close 1035 List(2016-07-26T21:00:00.000+0000, 2016-07-26T22:00:00.000+0000) Open 998 List(2016-07-26T21:00:00.000+0000, 2016-07-26T22:00:00.000+0000) Close 995 List(2016-07-26T22:00:00.000+0000, 2016-07-26T23:00:00.000+0000) Open 997 List(2016-07-26T22:00:00.000+0000, 2016-07-26T23:00:00.000+0000) Close 1036 List(2016-07-26T23:00:00.000+0000, 2016-07-27T00:00:00.000+0000) Close 950 List(2016-07-26T23:00:00.000+0000, 2016-07-27T00:00:00.000+0000) Open 1000 List(2016-07-27T00:00:00.000+0000, 2016-07-27T01:00:00.000+0000) Open 998 List(2016-07-27T00:00:00.000+0000, 2016-07-27T01:00:00.000+0000) Close 1008 List(2016-07-27T01:00:00.000+0000, 2016-07-27T02:00:00.000+0000) Close 1013 List(2016-07-27T01:00:00.000+0000, 2016-07-27T02:00:00.000+0000) Open 1004 List(2016-07-27T02:00:00.000+0000, 2016-07-27T03:00:00.000+0000) Open 992 List(2016-07-27T02:00:00.000+0000, 2016-07-27T03:00:00.000+0000) Close 971 List(2016-07-27T03:00:00.000+0000, 2016-07-27T04:00:00.000+0000) Open 1014 List(2016-07-27T03:00:00.000+0000, 2016-07-27T04:00:00.000+0000) Close 1025 List(2016-07-27T04:00:00.000+0000, 2016-07-27T05:00:00.000+0000) Open 995 List(2016

In [0]:
# Make this window a sliding window (30 minutes overlap): staticCountsSW
staticCountsSW = staticInputDF \
    .filter(col("action").isin("Open", "Close")) \
    .groupBy(
        window(col("time"), "1 hour", "30 minutes"),
        col("action")
    ) \
    .count() \
    .orderBy("window")

display(staticCountsSW)

window action count List(2016-07-26T02:00:00.000+0000, 2016-07-26T03:00:00.000+0000) Open 179 List(2016-07-26T02:00:00.000+0000, 2016-07-26T03:00:00.000+0000) Close 11 List(2016-07-26T02:30:00.000+0000, 2016-07-26T03:30:00.000+0000) Close 116 List(2016-07-26T02:30:00.000+0000, 2016-07-26T03:30:00.000+0000) Open 680 List(2016-07-26T03:00:00.000+0000, 2016-07-26T04:00:00.000+0000) Close 344 List(2016-07-26T03:00:00.000+0000, 2016-07-26T04:00:00.000+0000) Open 1001 List(2016-07-26T03:30:00.000+0000, 2016-07-26T04:30:00.000+0000) Close 581 List(2016-07-26T03:30:00.000+0000, 2016-07-26T04:30:00.000+0000) Open 993 List(2016-07-26T04:00:00.000+0000, 2016-07-26T05:00:00.000+0000) Close 815 List(2016-07-26T04:00:00.000+0000, 2016-07-26T05:00:00.000+0000) Open 999 List(2016-07-26T04:30:00.000+0000, 2016-07-26T05:30:00.000+0000) Close 987 List(2016-07-26T04:30:00.000+0000, 2016-07-26T05:30:00.000+0000) Open 1008 List(2016-07-26T05:00:00.000+0000, 2016-07-26T06:00:00.000+0000) Close 1003 List(2016-07-26T05:00:00.000+0000, 2016-07-26T06:00:00.000+0000) Open 1000 List(2016-07-26T05:30:00.000+0000, 2016-07-26T06:30:00.000+0000) Open 993 List(2016-07-26T05:30:00.000+0000, 2016-07-26T06:30:00.000+0000) Close 968 List(2016-07-26T06:00:00.000+0000, 2016-07-26T07:00:00.000+0000) Open 993 List(2016-07-26T06:00:00.000+0000, 2016-07-26T07:00:00.000+0000) Close 1011 List(2016-07-26T06:30:00.000+0000, 2016-07-26T07:30:00.000+0000) Close 1039 List(2016-07-26T06:30:00.000+0000, 2016-07-26T07:30:00.000+0000) Open 998 List(2016-07-26T07:00:00.000+0000, 2016-07-26T08:00:00.000+0000) Close 989 List(2016-07-26T07:00:00.000+0000, 2016-07-26T08:00:00.000+0000) Open 1008 List(2016-07-26T07:30:00.000+0000, 2016-07-26T08:30:00.000+0000) Close 953 List(2016-07-26T07:30:00.000+0000, 2016-07-26T08:30:00.000+0000) Open 1001 List(2016-07-26T08:00:00.000+0000, 2016-07-26T09:00:00.000+0000) Close 985 List(2016-07-26T08:00:00.000+0000, 2016-07-26T09:00:00.000+0000) Open 996 List(2016-07-26T08:30:00.000+0000, 2016-07-26T09:30:00.000+0000) Close 1025 List(2016-07-26T08:30:00.000+0000, 2016-07-26T09:30:00.000+0000) Open 1011 List(2016-07-26T09:00:00.000+0000, 2016-07-26T10:00:00.000+0000) Open 1000 List(2016-07-26T09:00:00.000+0000, 2016-07-26T10:00:00.000+0000) Close 983 List(2016-07-26T09:30:00.000+0000, 2016-07-26T10:30:00.000+0000) Open 991 List(2016-07-26T09:30:00.000+0000, 2016-07-26T10:30:00.000+0000) Close 978 List(2016-07-26T10:00:00.000+0000, 2016-07-26T11:00:00.000+0000) Close 1022 List(2016-07-26T10:00:00.000+0000, 2016-07-26T11:00:00.000+0000) Open 1007 List(2016-07-26T10:30:00.000+0000, 2016-07-26T11:30:00.000+0000) Open 999 List(2016-07-26T10:30:00.000+0000, 2016-07-26T11:30:00.000+0000) Close 1040 List(2016-07-26T11:00:00.000+0000, 2016-07-26T12:00:00.000+0000) Open 991 List(2016-07-26T11:00:00.000+0000, 2016-07-26T12:00:00.000+0000) Close 1028 List(2016-07-26T11:30:00.000+0000, 2016-07-26T12:30:00.000+0000) Close 997 List(2016-07-26T11:30:00.000+0000, 2016-07-26T12:30:00.000+0000) Open 996 List(2016-07-26T12:00:00.000+0000, 2016-07-26T13:00:00.000+0000) Close 960 List(2016-07-26T12:00:00.000+0000, 2016-07-26T13:00:00.000+0000) Open 996 List(2016-07-26T12:30:00.000+0000, 2016-07-26T13:30:00.000+0000) Open 1008 List(2016-07-26T12:30:00.000+0000, 2016-07-26T13:30:00.000+0000) Close 980 List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) Close 1028 List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) Open 1006 List(2016-07-26T13:30:00.000+0000, 2016-07-26T14:30:00.000+0000) Close 1042 List(2016-07-26T13:30:00.000+0000, 2016-07-26T14:30:00.000+0000) Open 994 List(2016-07-26T14:00:00.000+0000, 2016-07-26T15:00:00.000+0000) Close 994 List(2016-07-26T14:00:00.000+0000, 2016-07-26T15:00:00.000+0000) Open 991 List(2016-07-26T14:30:00.000+0000, 2016-07-26T15:30:00.000+0000) Open 1011 List(2016-07-26T14:30:00.000+0000, 2016-07-26T15:30:00.000+0000) Close 981 List(2016-07-26T15:00:00.000+0000, 2016-07-26T16:00:00.000+0000) Close 988 List(2016-07

In [0]:
# Register staticCountsDF (createOrReplaceTempView) as table 'static_counts'
staticCountsDF.createOrReplaceTempView("static_counts")

Now we can directly use SQL to query the table.

In [0]:
%sql
-- Count all Open and Close actions in the table static_counts  
SELECT action, SUM(count) AS total_count
FROM static_counts
GROUP BY action

action total_count Open 50000 Close 50000

In [0]:
%sql
-- How many actions (Close and Open separately) is within each time window (in the table static_counts)
-- Make a plot
SELECT window.start AS window_start, action, count
FROM static_counts
ORDER BY window_start, action

window_start action count 2016-07-26T02:00:00.000+0000 Close 11 2016-07-26T02:00:00.000+0000 Open 179 2016-07-26T03:00:00.000+0000 Close 344 2016-07-26T03:00:00.000+0000 Open 1001 2016-07-26T04:00:00.000+0000 Close 815 2016-07-26T04:00:00.000+0000 Open 999 2016-07-26T05:00:00.000+0000 Close 1003 2016-07-26T05:00:00.000+0000 Open 1000 2016-07-26T06:00:00.000+0000 Close 1011 2016-07-26T06:00:00.000+0000 Open 993 2016-07-26T07:00:00.000+0000 Close 989 2016-07-26T07:00:00.000+0000 Open 1008 2016-07-26T08:00:00.000+0000 Close 985 2016-07-26T08:00:00.000+0000 Open 996 2016-07-26T09:00:00.000+0000 Close 983 2016-07-26T09:00:00.000+0000 Open 1000 2016-07-26T10:00:00.000+0000 Close 1022 2016-07-26T10:00:00.000+0000 Open 1007 2016-07-26T11:00:00.000+0000 Close 1028 2016-07-26T11:00:00.000+0000 Open 991 2016-07-26T12:00:00.000+0000 Close 960 2016-07-26T12:00:00.000+0000 Open 996 2016-07-26T13:00:00.000+0000 Close 1028 2016-07-26T13:00:00.000+0000 Open 1006 2016-07-26T14:00:00.000+0000 Close 994 2016-07-26T14:00:00.000+0000 Open 991 2016-07-26T15:00:00.000+0000 Close 988 2016-07-26T15:00:00.000+0000 Open 1020 2016-07-26T16:00:00.000+0000 Close 984 2016-07-26T16:00:00.000+0000 Open 992 2016-07-26T17:00:00.000+0000 Close 1036 2016-07-26T17:00:00.000+0000 Open 990 2016-07-26T18:00:00.000+0000 Close 1001 2016-07-26T18:00:00.000+0000 Open 1004 2016-07-26T19:00:00.000+0000 Close 967 2016-07-26T19:00:00.000+0000 Open 998 2016-07-26T20:00:00.000+0000 Close 1035 2016-07-26T20:00:00.000+0000 Open 1010 2016-07-26T21:00:00.000+0000 Close 995 2016-07-26T21:00:00.000+0000 Open 998 2016-07-26T22:00:00.000+0000 Close 1036 2016-07-26T22:00:00.000+0000 Open 997 2016-07-26T23:00:00.000+0000 Close 950 2016-07-26T23:00:00.000+0000 Open 1000 2016-07-27T00:00:00.000+0000 Close 1008 2016-07-27T00:00:00.000+0000 Open 998 2016-07-27T01:00:00.000+0000 Close 1013 2016-07-27T01:00:00.000+0000 Open 1004 2016-07-27T02:00:00.000+0000 Close 971 2016-07-27T02:00:00.000+0000 Open 992 2016-07-27T03:00:00.000+0000 Close 1025 2016-07-27T03:00:00.000+0000 Open 1014 2016-07-27T04:00:00.000+0000 Close 989 2016-07-27T04:00:00.000+0000 Open 995 2016-07-27T05:00:00.000+0000 Close 987 2016-07-27T05:00:00.000+0000 Open 986 2016-07-27T06:00:00.000+0000 Close 1026 2016-07-27T06:00:00.000+0000 Open 1016 2016-07-27T07:00:00.000+0000 Close 982 2016-07-27T07:00:00.000+0000 Open 998 2016-07-27T08:00:00.000+0000 Close 1024 2016-07-27T08:00:00.000+0000 Open 1002 2016-07-27T09:00:00.000+0000 Close 990 2016-07-27T09:00:00.000+0000 Open 992 2016-07-27T10:00:00.000+0000 Close 1001 2016-07-27T10:00:00.000+0000 Open 1006 2016-07-27T11:00:00.000+0000 Close 1006 2016-07-27T11:00:00.000+0000 Open 998 2016-07-27T12:00:00.000+0000 Close 1035 2016-07-27T12:00:00.000+0000 Open 994 2016-07-27T13:00:00.000+0000 Close 986 2016-07-27T13:00:00.000+0000 Open 1008 2016-07-27T14:00:00.000+0000 Close 948 2016-07-27T14:00:00.000+0000 Open 984 2016-07-27T15:00:00.000+0000 Close 1018 2016-07-27T15:00:00.000+0000 Open 1017 2016-07-27T16:00:00.000+0000 Close 970 2016-07-27T16:00:00.000+0000 Open 992 2016-07-27T17:00:00.000+0000 Close 1020 2016-07-27T17:00:00.000+0000 Open 1007 2016-07-27T18:00:00.000+0000 Close 1036 2016-07-27T18:00:00.000+0000 Open 995 2016-07-27T19:00:00.000+0000 Close 969 2016-07-27T19:00:00.000+0000 Open 1007 2016-07-27T20:00:00.000+0000 Close 1025 2016-07-27T20:00:00.000+0000 Open 1005 2016-07-27T21:00:00.000+0000 Close 979 2016-07-27T21:00:00.000+0000 Open 998 2016-07-27T22:00:00.000+0000 Close 996 2016-07-27T22:00:00.000+0000 Open 986 2016-07-27T23:00:00.000+0000 Close 1011 2016-07-27T23:00:00.000+0000 Open 1008 2016-07-28T00:00:00.000+0000 Close 988 2016-07-28T00:00:00.000+0000 Open 1000 2016-07-28T01:00:00.000+0000 Close 1010 2016-07-28T01:00:00.000+0000 Open 1001 2016-07-28T02:00:00.000+0000 Close 1007 2016-07-28T02:00:00.000+0000 Open 1000 2016-07-28T03:00:00.000+0000 Close 993 2016-07-28T03:00:00.000+0000 Open 996 2016-07-28T04:00:00.000+0000 Close 960 2016-07-28T04:00:00.000+0000 Open 825 

Note the two ends of the graph. The close actions are generated such that they are after the corresponding open actions, so there are more "opens" in the beginning and more "closes" in the end.

## Demo: Stream Processing 
Now that we have analyzed the data interactively, let's convert this to a streaming query that continuously updates as data comes. Since we just have a static set of files, we are going to emulate a stream from them by reading one file at a time, in the chronological order they were created. The query we have to write is pretty much the same as the interactive query above.

In [0]:
from pyspark.sql.functions import *

# Read data from a file
# Similar to definition of staticInputDF above, just using `readStream` instead of `read`
streamingInputDF = (
  spark
    .readStream                       
    .schema(jsonSchema)               # Set the schema of the JSON data
    .option("maxFilesPerTrigger", 1)  # Treat a sequence of files as a stream by picking one file at a time
    .json(inputPath)
)

# Do some transformations
# Same query as staticInputDF
streamingCountsDF = (                 
  streamingInputDF
    .groupBy(
      streamingInputDF.action, 
      window(streamingInputDF.time, "1 hour"))
    .count()
)

# Is this DF actually a streaming DF?
streamingCountsDF.isStreaming

Out[15]: True

In [0]:
# Display input data
streamingInputDF.display()

time action 2016-07-26T02:45:07.000+0000 Open 2016-07-26T02:45:47.000+0000 Open 2016-07-26T02:46:42.000+0000 Open 2016-07-26T02:46:59.000+0000 Open 2016-07-26T02:47:05.000+0000 Open 2016-07-26T02:47:14.000+0000 Open 2016-07-26T02:47:25.000+0000 Open 2016-07-26T02:47:26.000+0000 Open 2016-07-26T02:47:28.000+0000 Open 2016-07-26T02:47:36.000+0000 Open 2016-07-26T02:47:44.000+0000 Open 2016-07-26T02:47:46.000+0000 Open 2016-07-26T02:47:47.000+0000 Open 2016-07-26T02:47:49.000+0000 Open 2016-07-26T02:47:51.000+0000 Open 2016-07-26T02:48:02.000+0000 Open 2016-07-26T02:48:05.000+0000 Open 2016-07-26T02:48:11.000+0000 Open 2016-07-26T02:48:17.000+0000 Open 2016-07-26T02:48:23.000+0000 Open 2016-07-26T02:48:42.000+0000 Open 2016-07-26T02:48:55.000+0000 Open 2016-07-26T02:49:04.000+0000 Open 2016-07-26T02:49:06.000+0000 Open 2016-07-26T02:49:09.000+0000 Open 2016-07-26T02:49:17.000+0000 Open 2016-07-26T02:49:26.000+0000 Open 2016-07-26T02:49:31.000+0000 Open 2016-07-26T02:49:35.000+0000 Open 2016-07-26T02:49:35.000+0000 Open 2016-07-26T02:49:41.000+0000 Open 2016-07-26T02:49:52.000+0000 Open 2016-07-26T02:50:02.000+0000 Open 2016-07-26T02:50:07.000+0000 Open 2016-07-26T02:50:10.000+0000 Open 2016-07-26T02:50:20.000+0000 Open 2016-07-26T02:50:24.000+0000 Open 2016-07-26T02:50:38.000+0000 Open 2016-07-26T02:50:42.000+0000 Close 2016-07-26T02:51:02.000+0000 Open 2016-07-26T02:51:20.000+0000 Open 2016-07-26T02:51:28.000+0000 Open 2016-07-26T02:51:29.000+0000 Open 2016-07-26T02:51:31.000+0000 Open 2016-07-26T02:51:43.000+0000 Open 2016-07-26T02:51:45.000+0000 Open 2016-07-26T02:51:49.000+0000 Open 2016-07-26T02:51:53.000+0000 Open 2016-07-26T02:51:57.000+0000 Open 2016-07-26T02:52:00.000+0000 Open 2016-07-26T02:52:05.000+0000 Open 2016-07-26T02:52:13.000+0000 Open 2016-07-26T02:52:19.000+0000 Open 2016-07-26T02:52:20.000+0000 Open 2016-07-26T02:52:21.000+0000 Open 2016-07-26T02:52:23.000+0000 Open 2016-07-26T02:52:24.000+0000 Open 2016-07-26T02:52:25.000+0000 Close 2016-07-26T02:52:25.000+0000 Open 2016-07-26T02:52:27.000+0000 Open 2016-07-26T02:52:32.000+0000 Open 2016-07-26T02:52:37.000+0000 Open 2016-07-26T02:52:39.000+0000 Open 2016-07-26T02:52:40.000+0000 Open 2016-07-26T02:52:40.000+0000 Open 2016-07-26T02:52:45.000+0000 Open 2016-07-26T02:52:46.000+0000 Open 2016-07-26T02:52:54.000+0000 Open 2016-07-26T02:52:55.000+0000 Open 2016-07-26T02:52:55.000+0000 Open 2016-07-26T02:52:58.000+0000 Open 2016-07-26T02:53:01.000+0000 Open 2016-07-26T02:53:04.000+0000 Open 2016-07-26T02:53:20.000+0000 Open 2016-07-26T02:53:21.000+0000 Open 2016-07-26T02:53:23.000+0000 Open 2016-07-26T02:53:30.000+0000 Open 2016-07-26T02:53:40.000+0000 Open 2016-07-26T02:53:41.000+0000 Open 2016-07-26T02:53:45.000+0000 Open 2016-07-26T02:53:45.000+0000 Close 2016-07-26T02:53:46.000+0000 Open 2016-07-26T02:53:51.000+0000 Open 2016-07-26T02:53:52.000+0000 Open 2016-07-26T02:53:52.000+0000 Open 2016-07-26T02:53:58.000+0000 Open 2016-07-26T02:54:03.000+0000 Open 2016-07-26T02:54:06.000+0000 Open 2016-07-26T02:54:22.000+0000 Open 2016-07-26T02:54:22.000+0000 Open 2016-07-26T02:54:22.000+0000 Open 2016-07-26T02:54:23.000+0000 Open 2016-07-26T02:54:27.000+0000 Open 2016-07-26T02:54:34.000+0000 Open 2016-07-26T02:54:35.000+0000 Open 2016-07-26T02:54:38.000+0000 Close 2016-07-26T02:54:40.000+0000 Open 2016-07-26T02:54:45.000+0000 Open 2016-07-26T02:54:46.000+0000 Open 2016-07-26T02:54:49.000+0000 Open 2016-07-26T02:54:51.000+0000 Open 2016-07-26T02:54:54.000+0000 Open 2016-07-26T02:54:56.000+0000 Close 2016-07-26T02:55:02.000+0000 Open 2016-07-26T02:55:03.000+0000 Open 2016-07-26T02:55:04.000+0000 Open 2016-07-26T02:55:06.000+0000 Open 2016-07-26T02:55:06.000+0000 Open 2016-07-26T02:55:10.000+0000 Open 2016-07-26T02:55:15.000+0000 Open 2016-07-26T02:55:17.000+0000 Open 2016-07-26T02:55:19.000+0000 Open 2016-07-26T02:55:19.000+0000 Open 2016-07-26T02:55:34.000+0000 Open 2016-07-26T02:55:39.000+0000 Open 2016-07-26T02:55:40.000+0000 Open 2016-07-26T02:55:47.000+0000 Open 2016-

In [0]:
# Display transformed data
streamingCountsDF.display()

action window count Close List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) 1028 Open List(2016-07-26T18:00:00.000+0000, 2016-07-26T19:00:00.000+0000) 1004 Close List(2016-07-27T02:00:00.000+0000, 2016-07-27T03:00:00.000+0000) 971 Open List(2016-07-27T04:00:00.000+0000, 2016-07-27T05:00:00.000+0000) 995 Open List(2016-07-27T05:00:00.000+0000, 2016-07-27T06:00:00.000+0000) 986 Open List(2016-07-26T05:00:00.000+0000, 2016-07-26T06:00:00.000+0000) 1000 Open List(2016-07-26T11:00:00.000+0000, 2016-07-26T12:00:00.000+0000) 991 Close List(2016-07-26T06:00:00.000+0000, 2016-07-26T07:00:00.000+0000) 1011 Close List(2016-07-27T05:00:00.000+0000, 2016-07-27T06:00:00.000+0000) 987 Open List(2016-07-26T10:00:00.000+0000, 2016-07-26T11:00:00.000+0000) 1007 Close List(2016-07-26T04:00:00.000+0000, 2016-07-26T05:00:00.000+0000) 815 Close List(2016-07-26T16:00:00.000+0000, 2016-07-26T17:00:00.000+0000) 984 Close List(2016-07-27T03:00:00.000+0000, 2016-07-27T04:00:00.000+0000) 1025 Open List(2016-07-27T07:00:00.000+0000, 2016-07-27T08:00:00.000+0000) 998 Open List(2016-07-27T18:00:00.000+0000, 2016-07-27T19:00:00.000+0000) 995 Close List(2016-07-27T13:00:00.000+0000, 2016-07-27T14:00:00.000+0000) 986 Close List(2016-07-26T12:00:00.000+0000, 2016-07-26T13:00:00.000+0000) 960 Close List(2016-07-27T08:00:00.000+0000, 2016-07-27T09:00:00.000+0000) 1024 Close List(2016-07-27T01:00:00.000+0000, 2016-07-27T02:00:00.000+0000) 1013 Open List(2016-07-27T19:00:00.000+0000, 2016-07-27T20:00:00.000+0000) 1007 Open List(2016-07-28T03:00:00.000+0000, 2016-07-28T04:00:00.000+0000) 996 Close List(2016-07-27T12:00:00.000+0000, 2016-07-27T13:00:00.000+0000) 1035 Close List(2016-07-28T00:00:00.000+0000, 2016-07-28T01:00:00.000+0000) 988 Close List(2016-07-27T16:00:00.000+0000, 2016-07-27T17:00:00.000+0000) 970 Close List(2016-07-26T08:00:00.000+0000, 2016-07-26T09:00:00.000+0000) 985 Close List(2016-07-27T14:00:00.000+0000, 2016-07-27T15:00:00.000+0000) 948 Open List(2016-07-27T11:00:00.000+0000, 2016-07-27T12:00:00.000+0000) 998 Open List(2016-07-28T04:00:00.000+0000, 2016-07-28T05:00:00.000+0000) 825 Open List(2016-07-26T19:00:00.000+0000, 2016-07-26T20:00:00.000+0000) 998 Close List(2016-07-26T11:00:00.000+0000, 2016-07-26T12:00:00.000+0000) 1028 Open List(2016-07-27T06:00:00.000+0000, 2016-07-27T07:00:00.000+0000) 1016 Open List(2016-07-27T21:00:00.000+0000, 2016-07-27T22:00:00.000+0000) 998 Open List(2016-07-27T16:00:00.000+0000, 2016-07-27T17:00:00.000+0000) 992 Close List(2016-07-28T01:00:00.000+0000, 2016-07-28T02:00:00.000+0000) 1010 Open List(2016-07-27T10:00:00.000+0000, 2016-07-27T11:00:00.000+0000) 1006 Close List(2016-07-26T17:00:00.000+0000, 2016-07-26T18:00:00.000+0000) 1036 Open List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) 1006 Open List(2016-07-27T17:00:00.000+0000, 2016-07-27T18:00:00.000+0000) 1007 Open List(2016-07-26T15:00:00.000+0000, 2016-07-26T16:00:00.000+0000) 1020 Open List(2016-07-27T12:00:00.000+0000, 2016-07-27T13:00:00.000+0000) 994 Open List(2016-07-26T04:00:00.000+0000, 2016-07-26T05:00:00.000+0000) 999 Close List(2016-07-26T18:00:00.000+0000, 2016-07-26T19:00:00.000+0000) 1001 Open List(2016-07-26T07:00:00.000+0000, 2016-07-26T08:00:00.000+0000) 1008 Open List(2016-07-26T20:00:00.000+0000, 2016-07-26T21:00:00.000+0000) 1010 Open List(2016-07-27T01:00:00.000+0000, 2016-07-27T02:00:00.000+0000) 1004 Close List(2016-07-27T15:00:00.000+0000, 2016-07-27T16:00:00.000+0000) 1018 Close List(2016-07-27T10:00:00.000+0000, 2016-07-27T11:00:00.000+0000) 1001 Close List(2016-07-27T00:00:00.000+0000, 2016-07-27T01:00:00.000+0000) 1008 Open List(2016-07-27T02:00:00.000+0000, 2016-07-27T03:00:00.000+0000) 992 Open List(2016-07-27T00:00:00.000+0000, 2016-07-27T01:00:00.000+0000) 998 Open List(2016-07-27T03:00:00.000+0000, 2016-07-27T04:00:00.000+0000) 1014 Close List(2016-07-27T06:00:00.000+0000, 2016-07-27T07:00:00.000+0000) 1026 Open List(2016-07-27T14:00:00.000+0000, 2016-07-27T15:00:00.000+0000) 984 Open Li

In [0]:
# Add aditional filter to transformed dataframe
streamingCountsDF.filter(streamingCountsDF.action == 'Open').display()

action window count Open List(2016-07-26T18:00:00.000+0000, 2016-07-26T19:00:00.000+0000) 1004 Open List(2016-07-27T04:00:00.000+0000, 2016-07-27T05:00:00.000+0000) 995 Open List(2016-07-27T05:00:00.000+0000, 2016-07-27T06:00:00.000+0000) 986 Open List(2016-07-26T05:00:00.000+0000, 2016-07-26T06:00:00.000+0000) 1000 Open List(2016-07-26T11:00:00.000+0000, 2016-07-26T12:00:00.000+0000) 991 Open List(2016-07-26T10:00:00.000+0000, 2016-07-26T11:00:00.000+0000) 1007 Open List(2016-07-27T07:00:00.000+0000, 2016-07-27T08:00:00.000+0000) 998 Open List(2016-07-27T18:00:00.000+0000, 2016-07-27T19:00:00.000+0000) 995 Open List(2016-07-27T19:00:00.000+0000, 2016-07-27T20:00:00.000+0000) 1007 Open List(2016-07-28T03:00:00.000+0000, 2016-07-28T04:00:00.000+0000) 996 Open List(2016-07-27T11:00:00.000+0000, 2016-07-27T12:00:00.000+0000) 998 Open List(2016-07-28T04:00:00.000+0000, 2016-07-28T05:00:00.000+0000) 825 Open List(2016-07-26T19:00:00.000+0000, 2016-07-26T20:00:00.000+0000) 998 Open List(2016-07-27T06:00:00.000+0000, 2016-07-27T07:00:00.000+0000) 1016 Open List(2016-07-27T21:00:00.000+0000, 2016-07-27T22:00:00.000+0000) 998 Open List(2016-07-27T16:00:00.000+0000, 2016-07-27T17:00:00.000+0000) 992 Open List(2016-07-27T10:00:00.000+0000, 2016-07-27T11:00:00.000+0000) 1006 Open List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) 1006 Open List(2016-07-27T17:00:00.000+0000, 2016-07-27T18:00:00.000+0000) 1007 Open List(2016-07-26T15:00:00.000+0000, 2016-07-26T16:00:00.000+0000) 1020 Open List(2016-07-27T12:00:00.000+0000, 2016-07-27T13:00:00.000+0000) 994 Open List(2016-07-26T04:00:00.000+0000, 2016-07-26T05:00:00.000+0000) 999 Open List(2016-07-26T07:00:00.000+0000, 2016-07-26T08:00:00.000+0000) 1008 Open List(2016-07-26T20:00:00.000+0000, 2016-07-26T21:00:00.000+0000) 1010 Open List(2016-07-27T01:00:00.000+0000, 2016-07-27T02:00:00.000+0000) 1004 Open List(2016-07-27T02:00:00.000+0000, 2016-07-27T03:00:00.000+0000) 992 Open List(2016-07-27T00:00:00.000+0000, 2016-07-27T01:00:00.000+0000) 998 Open List(2016-07-27T03:00:00.000+0000, 2016-07-27T04:00:00.000+0000) 1014 Open List(2016-07-27T14:00:00.000+0000, 2016-07-27T15:00:00.000+0000) 984 Open List(2016-07-26T14:00:00.000+0000, 2016-07-26T15:00:00.000+0000) 991 Open List(2016-07-26T12:00:00.000+0000, 2016-07-26T13:00:00.000+0000) 996 Open List(2016-07-28T02:00:00.000+0000, 2016-07-28T03:00:00.000+0000) 1000 Open List(2016-07-26T23:00:00.000+0000, 2016-07-27T00:00:00.000+0000) 1000 Open List(2016-07-26T16:00:00.000+0000, 2016-07-26T17:00:00.000+0000) 992 Open List(2016-07-26T22:00:00.000+0000, 2016-07-26T23:00:00.000+0000) 997 Open List(2016-07-26T03:00:00.000+0000, 2016-07-26T04:00:00.000+0000) 1001 Open List(2016-07-26T06:00:00.000+0000, 2016-07-26T07:00:00.000+0000) 993 Open List(2016-07-26T21:00:00.000+0000, 2016-07-26T22:00:00.000+0000) 998 Open List(2016-07-27T13:00:00.000+0000, 2016-07-27T14:00:00.000+0000) 1008 Open List(2016-07-27T08:00:00.000+0000, 2016-07-27T09:00:00.000+0000) 1002 Open List(2016-07-27T15:00:00.000+0000, 2016-07-27T16:00:00.000+0000) 1017 Open List(2016-07-28T01:00:00.000+0000, 2016-07-28T02:00:00.000+0000) 1001 Open List(2016-07-27T20:00:00.000+0000, 2016-07-27T21:00:00.000+0000) 1005 Open List(2016-07-28T00:00:00.000+0000, 2016-07-28T01:00:00.000+0000) 1000 Open List(2016-07-26T02:00:00.000+0000, 2016-07-26T03:00:00.000+0000) 179 Open List(2016-07-27T22:00:00.000+0000, 2016-07-27T23:00:00.000+0000) 986 Open List(2016-07-26T17:00:00.000+0000, 2016-07-26T18:00:00.000+0000) 990 Open List(2016-07-26T08:00:00.000+0000, 2016-07-26T09:00:00.000+0000) 996 Open List(2016-07-27T09:00:00.000+0000, 2016-07-27T10:00:00.000+0000) 992 Open List(2016-07-27T23:00:00.000+0000, 2016-07-28T00:00:00.000+0000) 1008 Open List(2016-07-26T09:00:00.000+0000, 2016-07-26T10:00:00.000+0000) 1000

As you can see, `streamingCountsDF` is a streaming Dataframe (`streamingCountsDF.isStreaming` was `true`). You can start streaming computation, by defining the sink and starting it. 
In our case, we want to interactively query the counts (same queries as above), so we will set the complete set of 1 hour counts to be in a in-memory table.

In [0]:
spark.conf.set("spark.sql.shuffle.partitions", "2")  # keep the size of shuffles small

query = (
  streamingCountsDF
    .writeStream
    .format("memory")        # memory = store in-memory table 
    .queryName("counts")     # counts = name of the in-memory table
    .outputMode("complete")  # complete = all the counts should be in the table
    #.trigger(processingTime='15 seconds')
    .start()
)

`query` is a handle to the streaming query that is running in the background. This query is continuously picking up files and updating the windowed counts. 

Note the status of query in the above cell. The progress bar shows that the query is active. 
Furthermore, if you expand the `> counts` above, you will find the number of files they have already processed. 

Let's wait a bit for a few files to be processed and then interactively query the in-memory `counts` table.

In [0]:
%sql
SELECT *
FROM counts

action window count Close List(2016-07-27T00:00:00.000+0000, 2016-07-27T01:00:00.000+0000) 1008 Open List(2016-07-26T22:00:00.000+0000, 2016-07-26T23:00:00.000+0000) 997 Open List(2016-07-27T14:00:00.000+0000, 2016-07-27T15:00:00.000+0000) 984 Close List(2016-07-26T14:00:00.000+0000, 2016-07-26T15:00:00.000+0000) 994 Open List(2016-07-28T04:00:00.000+0000, 2016-07-28T05:00:00.000+0000) 825 Close List(2016-07-27T14:00:00.000+0000, 2016-07-27T15:00:00.000+0000) 948 Close List(2016-07-26T23:00:00.000+0000, 2016-07-27T00:00:00.000+0000) 950 Open List(2016-07-27T06:00:00.000+0000, 2016-07-27T07:00:00.000+0000) 1016 Open List(2016-07-28T03:00:00.000+0000, 2016-07-28T04:00:00.000+0000) 996 Close List(2016-07-26T04:00:00.000+0000, 2016-07-26T05:00:00.000+0000) 815 Open List(2016-07-26T23:00:00.000+0000, 2016-07-27T00:00:00.000+0000) 1000 Close List(2016-07-27T19:00:00.000+0000, 2016-07-27T20:00:00.000+0000) 969 Close List(2016-07-27T05:00:00.000+0000, 2016-07-27T06:00:00.000+0000) 987 Open List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) 1006 Open List(2016-07-27T18:00:00.000+0000, 2016-07-27T19:00:00.000+0000) 995 Open List(2016-07-26T02:00:00.000+0000, 2016-07-26T03:00:00.000+0000) 179 Close List(2016-07-27T16:00:00.000+0000, 2016-07-27T17:00:00.000+0000) 970 Open List(2016-07-26T07:00:00.000+0000, 2016-07-26T08:00:00.000+0000) 1008 Open List(2016-07-26T12:00:00.000+0000, 2016-07-26T13:00:00.000+0000) 996 Open List(2016-07-27T11:00:00.000+0000, 2016-07-27T12:00:00.000+0000) 998 Close List(2016-07-27T01:00:00.000+0000, 2016-07-27T02:00:00.000+0000) 1013 Close List(2016-07-27T13:00:00.000+0000, 2016-07-27T14:00:00.000+0000) 986 Close List(2016-07-27T09:00:00.000+0000, 2016-07-27T10:00:00.000+0000) 990 Close List(2016-07-26T06:00:00.000+0000, 2016-07-26T07:00:00.000+0000) 1011 Close List(2016-07-27T10:00:00.000+0000, 2016-07-27T11:00:00.000+0000) 1001 Open List(2016-07-27T22:00:00.000+0000, 2016-07-27T23:00:00.000+0000) 986 Close List(2016-07-27T23:00:00.000+0000, 2016-07-28T00:00:00.000+0000) 1011 Open List(2016-07-27T20:00:00.000+0000, 2016-07-27T21:00:00.000+0000) 1005 Close List(2016-07-26T05:00:00.000+0000, 2016-07-26T06:00:00.000+0000) 1003 Close List(2016-07-26T21:00:00.000+0000, 2016-07-26T22:00:00.000+0000) 995 Close List(2016-07-27T15:00:00.000+0000, 2016-07-27T16:00:00.000+0000) 1018 Close List(2016-07-28T04:00:00.000+0000, 2016-07-28T05:00:00.000+0000) 960 Close List(2016-07-26T17:00:00.000+0000, 2016-07-26T18:00:00.000+0000) 1036 Close List(2016-07-28T02:00:00.000+0000, 2016-07-28T03:00:00.000+0000) 1007 Open List(2016-07-27T01:00:00.000+0000, 2016-07-27T02:00:00.000+0000) 1004 Close List(2016-07-26T20:00:00.000+0000, 2016-07-26T21:00:00.000+0000) 1035 Close List(2016-07-26T16:00:00.000+0000, 2016-07-26T17:00:00.000+0000) 984 Close List(2016-07-27T21:00:00.000+0000, 2016-07-27T22:00:00.000+0000) 979 Close List(2016-07-28T03:00:00.000+0000, 2016-07-28T04:00:00.000+0000) 993 Close List(2016-07-26T07:00:00.000+0000, 2016-07-26T08:00:00.000+0000) 989 Open List(2016-07-27T10:00:00.000+0000, 2016-07-27T11:00:00.000+0000) 1006 Close List(2016-07-27T07:00:00.000+0000, 2016-07-27T08:00:00.000+0000) 982 Close List(2016-07-26T15:00:00.000+0000, 2016-07-26T16:00:00.000+0000) 988 Close List(2016-07-28T00:00:00.000+0000, 2016-07-28T01:00:00.000+0000) 988 Open List(2016-07-27T04:00:00.000+0000, 2016-07-27T05:00:00.000+0000) 995 Open List(2016-07-26T09:00:00.000+0000, 2016-07-26T10:00:00.000+0000) 1000 Close List(2016-07-26T08:00:00.000+0000, 2016-07-26T09:00:00.000+0000) 985 Close List(2016-07-26T19:00:00.000+0000, 2016-07-26T20:00:00.000+0000) 967 Open List(2016-07-27T23:00:00.000+0000, 2016-07-28T00:00:00.000+0000) 1008 Close List(2016-07-26T13:00:00.000+0000, 2016-07-26T14:00:00.000+0000) 1028 Close List(2016-07-27T20:00:00.000+0000, 2016-07-27T21:00:00.000+0000) 1025 Close List(2016-07-27T22:00:00.000+0000, 2016-07-27T23:00:00.000+0000) 996 Open List(2016-07-27T05:00:00.000+0000, 2016-07-27T06:00:00.000+0000) 986 Open

In [0]:
from time import sleep
sleep(5)  # wait a bit for computation to start

In [0]:
%sql
select action, date_format(window.end, "MMM-dd HH:mm") as time, count
from counts
order by time, action

action time count Close Jul-26 03:00 11 Open Jul-26 03:00 179 Close Jul-26 04:00 344 Open Jul-26 04:00 1001 Close Jul-26 05:00 815 Open Jul-26 05:00 999 Close Jul-26 06:00 1003 Open Jul-26 06:00 1000 Close Jul-26 07:00 1011 Open Jul-26 07:00 993 Close Jul-26 08:00 989 Open Jul-26 08:00 1008 Close Jul-26 09:00 985 Open Jul-26 09:00 996 Close Jul-26 10:00 983 Open Jul-26 10:00 1000 Close Jul-26 11:00 1022 Open Jul-26 11:00 1007 Close Jul-26 12:00 1028 Open Jul-26 12:00 991 Close Jul-26 13:00 960 Open Jul-26 13:00 996 Close Jul-26 14:00 1028 Open Jul-26 14:00 1006 Close Jul-26 15:00 994 Open Jul-26 15:00 991 Close Jul-26 16:00 988 Open Jul-26 16:00 1020 Close Jul-26 17:00 984 Open Jul-26 17:00 992 Close Jul-26 18:00 1036 Open Jul-26 18:00 990 Close Jul-26 19:00 1001 Open Jul-26 19:00 1004 Close Jul-26 20:00 967 Open Jul-26 20:00 998 Close Jul-26 21:00 1035 Open Jul-26 21:00 1010 Close Jul-26 22:00 995 Open Jul-26 22:00 998 Close Jul-26 23:00 1036 Open Jul-26 23:00 997 Close Jul-27 00:00 950 Open Jul-27 00:00 1000 Close Jul-27 01:00 1008 Open Jul-27 01:00 998 Close Jul-27 02:00 1013 Open Jul-27 02:00 1004 Close Jul-27 03:00 971 Open Jul-27 03:00 992 Close Jul-27 04:00 1025 Open Jul-27 04:00 1014 Close Jul-27 05:00 989 Open Jul-27 05:00 995 Close Jul-27 06:00 987 Open Jul-27 06:00 986 Close Jul-27 07:00 1026 Open Jul-27 07:00 1016 Close Jul-27 08:00 982 Open Jul-27 08:00 998 Close Jul-27 09:00 1024 Open Jul-27 09:00 1002 Close Jul-27 10:00 990 Open Jul-27 10:00 992 Close Jul-27 11:00 1001 Open Jul-27 11:00 1006 Close Jul-27 12:00 1006 Open Jul-27 12:00 998 Close Jul-27 13:00 1035 Open Jul-27 13:00 994 Close Jul-27 14:00 986 Open Jul-27 14:00 1008 Close Jul-27 15:00 948 Open Jul-27 15:00 984 Close Jul-27 16:00 1018 Open Jul-27 16:00 1017 Close Jul-27 17:00 970 Open Jul-27 17:00 992 Close Jul-27 18:00 1020 Open Jul-27 18:00 1007 Close Jul-27 19:00 1036 Open Jul-27 19:00 995 Close Jul-27 20:00 969 Open Jul-27 20:00 1007 Close Jul-27 21:00 1025 Open Jul-27 21:00 1005 Close Jul-27 22:00 979 Open Jul-27 22:00 998 Close Jul-27 23:00 996 Open Jul-27 23:00 986 Close Jul-28 00:00 1011 Open Jul-28 00:00 1008 Close Jul-28 01:00 988 Open Jul-28 01:00 1000 Close Jul-28 02:00 1010 Open Jul-28 02:00 1001 Close Jul-28 03:00 1007 Open Jul-28 03:00 1000 Close Jul-28 04:00 993 Open Jul-28 04:00 996 Close Jul-28 05:00 960 Open Jul-28 05:00 825 Close Jul-28 06:00 671 Close Jul-28 07:00 191

We see the timeline of windowed counts (similar to the static one earlier) building up. If we keep running this interactive query repeatedly, we will see the latest updated counts which the streaming query is updating in the background.

In [0]:
sleep(5)  # wait a bit more for more data to be computed

In [0]:
%sql select action, date_format(window.end, "MMM-dd HH:mm") as time, count from counts order by time, action

action time count Close Jul-26 03:00 11 Open Jul-26 03:00 179 Close Jul-26 04:00 344 Open Jul-26 04:00 1001 Close Jul-26 05:00 815 Open Jul-26 05:00 999 Close Jul-26 06:00 1003 Open Jul-26 06:00 1000 Close Jul-26 07:00 1011 Open Jul-26 07:00 993 Close Jul-26 08:00 989 Open Jul-26 08:00 1008 Close Jul-26 09:00 985 Open Jul-26 09:00 996 Close Jul-26 10:00 983 Open Jul-26 10:00 1000 Close Jul-26 11:00 1022 Open Jul-26 11:00 1007 Close Jul-26 12:00 1028 Open Jul-26 12:00 991 Close Jul-26 13:00 960 Open Jul-26 13:00 996 Close Jul-26 14:00 1028 Open Jul-26 14:00 1006 Close Jul-26 15:00 994 Open Jul-26 15:00 991 Close Jul-26 16:00 988 Open Jul-26 16:00 1020 Close Jul-26 17:00 984 Open Jul-26 17:00 992 Close Jul-26 18:00 1036 Open Jul-26 18:00 990 Close Jul-26 19:00 1001 Open Jul-26 19:00 1004 Close Jul-26 20:00 967 Open Jul-26 20:00 998 Close Jul-26 21:00 1035 Open Jul-26 21:00 1010 Close Jul-26 22:00 995 Open Jul-26 22:00 998 Close Jul-26 23:00 1036 Open Jul-26 23:00 997 Close Jul-27 00:00 950 Open Jul-27 00:00 1000 Close Jul-27 01:00 1008 Open Jul-27 01:00 998 Close Jul-27 02:00 1013 Open Jul-27 02:00 1004 Close Jul-27 03:00 971 Open Jul-27 03:00 992 Close Jul-27 04:00 1025 Open Jul-27 04:00 1014 Close Jul-27 05:00 989 Open Jul-27 05:00 995 Close Jul-27 06:00 987 Open Jul-27 06:00 986 Close Jul-27 07:00 1026 Open Jul-27 07:00 1016 Close Jul-27 08:00 982 Open Jul-27 08:00 998 Close Jul-27 09:00 1024 Open Jul-27 09:00 1002 Close Jul-27 10:00 990 Open Jul-27 10:00 992 Close Jul-27 11:00 1001 Open Jul-27 11:00 1006 Close Jul-27 12:00 1006 Open Jul-27 12:00 998 Close Jul-27 13:00 1035 Open Jul-27 13:00 994 Close Jul-27 14:00 986 Open Jul-27 14:00 1008 Close Jul-27 15:00 948 Open Jul-27 15:00 984 Close Jul-27 16:00 1018 Open Jul-27 16:00 1017 Close Jul-27 17:00 970 Open Jul-27 17:00 992 Close Jul-27 18:00 1020 Open Jul-27 18:00 1007 Close Jul-27 19:00 1036 Open Jul-27 19:00 995 Close Jul-27 20:00 969 Open Jul-27 20:00 1007 Close Jul-27 21:00 1025 Open Jul-27 21:00 1005 Close Jul-27 22:00 979 Open Jul-27 22:00 998 Close Jul-27 23:00 996 Open Jul-27 23:00 986 Close Jul-28 00:00 1011 Open Jul-28 00:00 1008 Close Jul-28 01:00 988 Open Jul-28 01:00 1000 Close Jul-28 02:00 1010 Open Jul-28 02:00 1001 Close Jul-28 03:00 1007 Open Jul-28 03:00 1000 Close Jul-28 04:00 993 Open Jul-28 04:00 996 Close Jul-28 05:00 960 Open Jul-28 05:00 825 Close Jul-28 06:00 671 Close Jul-28 07:00 191

In [0]:
sleep(5)  # wait a bit more for more data to be computed

In [0]:
%sql select action, date_format(window.end, "MMM-dd HH:mm") as time, count from counts order by time, action

action time count Close Jul-26 03:00 11 Open Jul-26 03:00 179 Close Jul-26 04:00 344 Open Jul-26 04:00 1001 Close Jul-26 05:00 815 Open Jul-26 05:00 999 Close Jul-26 06:00 1003 Open Jul-26 06:00 1000 Close Jul-26 07:00 1011 Open Jul-26 07:00 993 Close Jul-26 08:00 989 Open Jul-26 08:00 1008 Close Jul-26 09:00 985 Open Jul-26 09:00 996 Close Jul-26 10:00 983 Open Jul-26 10:00 1000 Close Jul-26 11:00 1022 Open Jul-26 11:00 1007 Close Jul-26 12:00 1028 Open Jul-26 12:00 991 Close Jul-26 13:00 960 Open Jul-26 13:00 996 Close Jul-26 14:00 1028 Open Jul-26 14:00 1006 Close Jul-26 15:00 994 Open Jul-26 15:00 991 Close Jul-26 16:00 988 Open Jul-26 16:00 1020 Close Jul-26 17:00 984 Open Jul-26 17:00 992 Close Jul-26 18:00 1036 Open Jul-26 18:00 990 Close Jul-26 19:00 1001 Open Jul-26 19:00 1004 Close Jul-26 20:00 967 Open Jul-26 20:00 998 Close Jul-26 21:00 1035 Open Jul-26 21:00 1010 Close Jul-26 22:00 995 Open Jul-26 22:00 998 Close Jul-26 23:00 1036 Open Jul-26 23:00 997 Close Jul-27 00:00 950 Open Jul-27 00:00 1000 Close Jul-27 01:00 1008 Open Jul-27 01:00 998 Close Jul-27 02:00 1013 Open Jul-27 02:00 1004 Close Jul-27 03:00 971 Open Jul-27 03:00 992 Close Jul-27 04:00 1025 Open Jul-27 04:00 1014 Close Jul-27 05:00 989 Open Jul-27 05:00 995 Close Jul-27 06:00 987 Open Jul-27 06:00 986 Close Jul-27 07:00 1026 Open Jul-27 07:00 1016 Close Jul-27 08:00 982 Open Jul-27 08:00 998 Close Jul-27 09:00 1024 Open Jul-27 09:00 1002 Close Jul-27 10:00 990 Open Jul-27 10:00 992 Close Jul-27 11:00 1001 Open Jul-27 11:00 1006 Close Jul-27 12:00 1006 Open Jul-27 12:00 998 Close Jul-27 13:00 1035 Open Jul-27 13:00 994 Close Jul-27 14:00 986 Open Jul-27 14:00 1008 Close Jul-27 15:00 948 Open Jul-27 15:00 984 Close Jul-27 16:00 1018 Open Jul-27 16:00 1017 Close Jul-27 17:00 970 Open Jul-27 17:00 992 Close Jul-27 18:00 1020 Open Jul-27 18:00 1007 Close Jul-27 19:00 1036 Open Jul-27 19:00 995 Close Jul-27 20:00 969 Open Jul-27 20:00 1007 Close Jul-27 21:00 1025 Open Jul-27 21:00 1005 Close Jul-27 22:00 979 Open Jul-27 22:00 998 Close Jul-27 23:00 996 Open Jul-27 23:00 986 Close Jul-28 00:00 1011 Open Jul-28 00:00 1008 Close Jul-28 01:00 988 Open Jul-28 01:00 1000 Close Jul-28 02:00 1010 Open Jul-28 02:00 1001 Close Jul-28 03:00 1007 Open Jul-28 03:00 1000 Close Jul-28 04:00 993 Open Jul-28 04:00 996 Close Jul-28 05:00 960 Open Jul-28 05:00 825 Close Jul-28 06:00 671 Close Jul-28 07:00 191

Also, let's see the total number of "opens" and "closes".

In [0]:
%sql 
select action, sum(count) as total_count 
from counts 
group by action 
order by action

action total_count Close 50000 Open 50000

If you keep running the above query repeatedly, you will always find that the number of "opens" is more than the number of "closes", as expected in a data stream where a "close" always appear after corresponding "open". This shows that Structured Streaming ensures **prefix integrity**. Read the blog posts linked below if you want to know more.

Note that there are only a few files, so consuming all of them there will be no updates to the counts. Rerun the query if you want to interact with the streaming query again.

Finally, you can stop the query running in the background, either by clicking on the 'Cancel' link in the cell of the query, or by executing `query.stop()`. Either way, when the query is stopped, the status of the corresponding cell above will automatically update to `TERMINATED`.

In [0]:
query.stop()

### IoT data

Develop a streaming example on `IoT device`dataset:

- inspect the dataset
- ask yourself couple of questions about the data and try to answer them (eg. how many steps users do, how many calories do they burn...)
- you read the data in streaming fashion (file by file) and keep the data for only one company? Here are some hints:
  - you can find the schema in the readme file 
  - as above, use this option: .option("maxFilesPerTrigger", 1)
  - use user_id or device_id for grouping
  - use timestamp for window definition
  - you can try streaming joins with the user data (/databricks-datasets/iot-stream/data-user/userData.csv). Here is the doc: https://spark.apache.org/docs/latest/structured-streaming-programming-guide.html#join-operations

In [0]:
# Iot stream dataset
display(dbutils.fs.ls('/databricks-datasets/iot-stream/'))

path name size modificationTime dbfs:/databricks-datasets/iot-stream/README.md README.md 1596 1532465738000 dbfs:/databricks-datasets/iot-stream/data-device/ data-device/ 0 0 dbfs:/databricks-datasets/iot-stream/data-user/ data-user/ 0 0

In [0]:
# Read the README file
readme_path = '/databricks-datasets/iot-stream/README.md'
readme_df = spark.read.text(readme_path)
display(readme_df)


value ========================================== IOT Device Data ========================================== This dataset was created by Databricks. It contains fake generated data in json and csv formats. e.g. `{"user_id": 12, "calories_burnt": 489.79998779296875, "num_steps": 9796, "miles_walked": 4.8979997634887695, "time_stamp": "2018-07-24 03:54:00.893775", "device_id": 10}` ========================================= Data Set Information ========================================= Schema for data-device: ``` [StructField(id,LongType,false), StructField(user_id,LongType,true), StructField(device_id,LongType,true), StructField(num_steps,LongType,true), StructField(miles_walked,FloatType,true), StructField(calories_burnt,FloatType,true), StructField(timestamp,StringType,true), StructField(value,StringType,true)] ``` Schema for data-user: ``` [StructField(userid,IntegerType,true), StructField(gender,StringType,true), StructField(age,IntegerType,true), StructField(height,IntegerType,true), StructField(weight,IntegerType,true), StructField(smoker,StringType,true), StructField(familyhistory,StringType,true), StructField(cholestlevs,StringType,true), StructField(bp,StringType,true), StructField(risk,IntegerType,true)] ``` ========================================= License and/or Citation ========================================= Copyright (2018) Databricks, Inc. This dataset is licensed under a Creative Commons Attribution 4.0 International License .

In [0]:
# Define the schema (copy from the README) data-device
from pyspark.sql.types import StructType, StructField, LongType, FloatType, StringType

device_schema = StructType([
    StructField("id", LongType(), False),
    StructField("user_id", LongType(), True),
    StructField("device_id", LongType(), True),
    StructField("num_steps", LongType(), True),
    StructField("miles_walked", FloatType(), True),
    StructField("calories_burnt", FloatType(), True),
    StructField("timestamp", StringType(), True),
    StructField("value", StringType(), True)
])


In [0]:
# Open one file to see how the data looks like (as a static dataframe)
files = dbutils.fs.ls('/databricks-datasets/iot-stream/data-device/')
first_file_path = files[0].path

# Read the first file only
single_file_df = spark.read.schema(device_schema).json(first_file_path)
display(single_file_df)


id user_id device_id num_steps miles_walked calories_burnt timestamp value 0 36 9 3278 1.639 163.90001 2018-07-20 07:34:28.546561 {"user_id": 36, "calories_burnt": 163.90000915527344, "num_steps": 3278, "miles_walked": 1.6390000581741333, "time_stamp": "2018-07-20 07:34:28.546561", "device_id": 9} 1 26 20 10293 5.1465 514.65 2018-07-24 08:13:49.546627 {"user_id": 26, "calories_burnt": 514.6500244140625, "num_steps": 10293, "miles_walked": 5.146500110626221, "time_stamp": "2018-07-24 08:13:49.546627", "device_id": 20} 2 11 9 5574 2.787 278.69998 2018-07-24 18:41:57.546657 {"user_id": 11, "calories_burnt": 278.6999816894531, "num_steps": 5574, "miles_walked": 2.7869999408721924, "time_stamp": "2018-07-24 18:41:57.546657", "device_id": 9} 3 13 4 5590 2.795 279.5 2018-07-21 08:40:41.546750 {"user_id": 13, "calories_burnt": 279.5, "num_steps": 5590, "miles_walked": 2.7950000762939453, "time_stamp": "2018-07-21 08:40:41.546750", "device_id": 4} 4 32 1 8373 4.1865 418.65 2018-07-24 08:08:55.546779 {"user_id": 32, "calories_burnt": 418.6499938964844, "num_steps": 8373, "miles_walked": 4.186500072479248, "time_stamp": "2018-07-24 08:08:55.546779", "device_id": 1} 5 8 1 11052 5.526 552.6 2018-07-19 22:58:37.546806 {"user_id": 8, "calories_burnt": 552.5999755859375, "num_steps": 11052, "miles_walked": 5.526000022888184, "time_stamp": "2018-07-19 22:58:37.546806", "device_id": 1} 6 33 9 3154 1.577 157.7 2018-07-20 18:54:52.546839 {"user_id": 33, "calories_burnt": 157.6999969482422, "num_steps": 3154, "miles_walked": 1.5770000219345093, "time_stamp": "2018-07-20 18:54:52.546839", "device_id": 9} 7 18 16 1659 0.8295 82.950005 2018-07-22 07:16:44.546870 {"user_id": 18, "calories_burnt": 82.95000457763672, "num_steps": 1659, "miles_walked": 0.8295000195503235, "time_stamp": "2018-07-22 07:16:44.546870", "device_id": 16} 8 15 10 10620 5.31 531.0 2018-07-23 17:06:48.546899 {"user_id": 15, "calories_burnt": 531.0, "num_steps": 10620, "miles_walked": 5.309999942779541, "time_stamp": "2018-07-23 17:06:48.546899", "device_id": 10} 9 9 3 8374 4.187 418.69998 2018-07-21 08:45:33.546930 {"user_id": 9, "calories_burnt": 418.6999816894531, "num_steps": 8374, "miles_walked": 4.186999797821045, "time_stamp": "2018-07-21 08:45:33.546930", "device_id": 3} 10 21 17 4963 2.4815 248.15 2018-07-21 14:15:28.546956 {"user_id": 21, "calories_burnt": 248.14999389648438, "num_steps": 4963, "miles_walked": 2.4814999103546143, "time_stamp": "2018-07-21 14:15:28.546956", "device_id": 17} 11 21 17 2323 1.1615 116.149994 2018-07-21 21:21:54.546981 {"user_id": 21, "calories_burnt": 116.14999389648438, "num_steps": 2323, "miles_walked": 1.1614999771118164, "time_stamp": "2018-07-21 21:21:54.546981", "device_id": 17} 12 24 20 2165 1.0825 108.25 2018-07-23 03:52:49.547005 {"user_id": 24, "calories_burnt": 108.25, "num_steps": 2165, "miles_walked": 1.0824999809265137, "time_stamp": "2018-07-23 03:52:49.547005", "device_id": 20} 13 11 14 8411 4.2055 420.55002 2018-07-24 01:54:29.547033 {"user_id": 11, "calories_burnt": 420.5500183105469, "num_steps": 8411, "miles_walked": 4.20550012588501, "time_stamp": "2018-07-24 01:54:29.547033", "device_id": 14} 14 10 10 1378 0.689 68.9 2018-07-20 17:37:08.547059 {"user_id": 10, "calories_burnt": 68.9000015258789, "num_steps": 1378, "miles_walked": 0.6890000104904175, "time_stamp": "2018-07-20 17:37:08.547059", "device_id": 10} 15 16 10 7785 3.8925 389.25 2018-07-24 16:38:23.547086 {"user_id": 16, "calories_burnt": 389.25, "num_steps": 7785, "miles_walked": 3.8924999237060547, "time_stamp": "2018-07-24 16:38:23.547086", "device_id": 10} 16 16 2 3500 1.75 175.0 2018-07-21 16:07:55.547114 {"user_id": 16, "calories_burnt": 175.0, "num_steps": 3500, "miles_walked": 1.75, "time_stamp": "2018-07-21 16:07:55.547114", "device_id": 2} 17 13 5 11761 5.8805 588.05 2018-07-22 18:41:52.547146 {"user_id": 13, "calories_burnt": 588.0499877929688, "num_steps": 11761, "miles_walked": 5.880499839782715, "time_stamp": "2018-07-22 18:41:52.547146", "device_id

In [0]:
# Define your streaming dataframe
streaming_device_df = (
    spark.readStream
    .schema(device_schema)
    .option("maxFilesPerTrigger", 1)
    .json("/databricks-datasets/iot-stream/data-device/")
)

# Preview schema
streaming_device_df.printSchema()

root
 |-- id: long (nullable = true)
 |-- user_id: long (nullable = true)
 |-- device_id: long (nullable = true)
 |-- num_steps: long (nullable = true)
 |-- miles_walked: float (nullable = true)
 |-- calories_burnt: float (nullable = true)
 |-- timestamp: string (nullable = true)
 |-- value: string (nullable = true)



In [0]:
# Define your transformations
from pyspark.sql.functions import to_timestamp

stream_transformed_df = streaming_device_df.withColumn(
    "event_time", to_timestamp("timestamp")
)
stream_transformed_df = stream_transformed_df.select(
    "id", "user_id", "device_id", "num_steps", "miles_walked",
    "calories_burnt", "event_time"
)
from pyspark.sql.functions import window

steps_per_user = (
    stream_transformed_df
    .withWatermark("event_time", "1 minute")
    .groupBy(
        window("event_time", "1 minute"),
        "user_id"
    )
    .sum("num_steps")
    .withColumnRenamed("sum(num_steps)", "total_steps")
)


In [0]:
# Define the sink and start streaming
query = (
    steps_per_user.writeStream
        .outputMode("complete")
        .format("memory")
        .queryName("iot_analytics")
        .start()
)


In [0]:
%sql
-- visualize your streaming analytics
SELECT *
FROM iot_analytics
ORDER BY window.start



window user_id total_steps List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 1 7635 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 38 61606 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 32 23106 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 26 5357 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 14 9684 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 12 2408 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 17 22819 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 24 8084 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 2 29440 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 36 1083 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 16 6515 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 6 5732 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 20 2163 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 15 30058 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 7 72957 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 29 8118 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 21 1309 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 28 42140 List(2018-07-19T18:31:00.000+0000, 2018-07-19T18:32:00.000+0000) 22 8578 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 11 14279 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 32 39600 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 17 14693 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 9 43127 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 26 27776 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 34 1157 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 21 50130 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 23 3527 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 12 37124 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 33 57202 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 6 7550 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 29 17589 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 25 18711 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 18 51540 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 14 23486 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 16 24175 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 10 22500 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 4 30596 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 15 17847 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 5 9464 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 24 32403 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 28 10236 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 20 12515 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 8 3509 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 1 10402 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 38 42043 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 30 13167 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 31 45000 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 19 27912 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 13 68555 List(2018-07-19T18:32:00.000+0000, 2018-07-19T18:33:00.000+0000) 3 21424 List(2018-07-19T18:33:00.000+0000, 2018-07-19T18:34:00.000+0000) 31 4368 List(2018-07-19T18:33:00.000+0000, 2018-07-19T18:34:00.000+0000) 34 1660 List(2018-07-19T18:33:00.000+0000, 2018-07-19T18:34:00.000+0000) 6 34578 List(2018-07-19T18:33:00.000+0000, 2018-07-19T18:34:00.000+0000) 30 29798 List(201